In [1]:
!wget -nc https://raw.githubusercontent.com/askplatypus/wikidata-simplequestions/master/annotated_wd_data_train_answerable.txt
!wget -nc https://raw.githubusercontent.com/askplatypus/wikidata-simplequestions/master/annotated_wd_data_valid_answerable.txt
!wget -nc https://raw.githubusercontent.com/askplatypus/wikidata-simplequestions/master/annotated_wd_data_test_answerable.txt

--2023-12-30 12:56:11--  https://raw.githubusercontent.com/askplatypus/wikidata-simplequestions/master/annotated_wd_data_train_answerable.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1193868 (1,1M) [text/plain]
Saving to: ‘annotated_wd_data_train_answerable.txt’

annotated_wd_data_t 100%[===================>]   1,14M  6,45MB/s    in 0,2s    

2023-12-30 12:56:11 (6,45 MB/s) - ‘annotated_wd_data_train_answerable.txt’ saved [1193868/1193868]

--2023-12-30 12:56:11--  https://raw.githubusercontent.com/askplatypus/wikidata-simplequestions/master/annotated_wd_data_valid_answerable.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubu

In [2]:
import pandas as pd
import datasets 
import numpy as np
import random
import logging

np.random.seed(8)
random.seed(8)

/home/salnikov/.cache/pypoetry/virtualenvs/kgqa-signatures-J3ZJKtLx-py3.10/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
dataset = datasets.DatasetDict()
for split, data_path in [
    ("train", "annotated_wd_data_train_answerable.txt"),
    ("valid", "annotated_wd_data_valid_answerable.txt"),
    ("test", "annotated_wd_data_test_answerable.txt"),
]:
    df = pd.read_csv(data_path, names=['subject', 'property', 'object', 'question'], sep='\t')
    dataset[split] = datasets.Dataset.from_pandas(df)

dataset

DatasetDict({
    train: Dataset({
        features: ['subject', 'property', 'object', 'question'],
        num_rows: 19481
    })
    valid: Dataset({
        features: ['subject', 'property', 'object', 'question'],
        num_rows: 2821
    })
    test: Dataset({
        features: ['subject', 'property', 'object', 'question'],
        num_rows: 5622
    })
})

In [4]:
import os
import os.path
import pickle
import warnings

from joblib import register_store_backend, numpy_pickle
from joblib._store_backends import FileSystemStoreBackend, CacheWarning


class FileSystemStoreBackendNoNumpy(FileSystemStoreBackend):
    NAME = "no_numpy"

    def load_item(self, path, verbose=1, msg=None):
        """Load an item from the store given its path as a list of
           strings."""
        full_path = os.path.join(self.location, *path)

        if verbose > 1:
            if verbose < 10:
                print('{0}...'.format(msg))
            else:
                print('{0} from {1}'.format(msg, full_path))

        mmap_mode = (None if not hasattr(self, 'mmap_mode')
                     else self.mmap_mode)

        filename = os.path.join(full_path, 'output.pkl')
        if not self._item_exists(filename):
            raise KeyError("Non-existing item (may have been "
                           "cleared).\nFile %s does not exist" % filename)

        # file-like object cannot be used when mmap_mode is set
        if mmap_mode is None:
            with self._open_item(filename, "rb") as f:
                item = pickle.load(f)
        else:
            item = numpy_pickle.load(filename, mmap_mode=mmap_mode)
        return item

    def dump_item(self, path, item, verbose=1):
        """Dump an item in the store at the path given as a list of
           strings."""
        try:
            item_path = os.path.join(self.location, *path)
            if not self._item_exists(item_path):
                self.create_location(item_path)
            filename = os.path.join(item_path, 'output.pkl')
            if verbose > 10:
                print('Persisting in %s' % item_path)

            def write_func(to_write, dest_filename):
                mmap_mode = (None if not hasattr(self, 'mmap_mode')
                             else self.mmap_mode)
                with self._open_item(dest_filename, "wb") as f:
                    try:
                        if mmap_mode is None:
                            pickle.dump(to_write, f)
                        else:
                            numpy_pickle.dump(to_write, f, compress=self.compress)
                    except pickle.PicklingError as e:
                        # TODO(1.5) turn into error
                        warnings.warn(
                            "Unable to cache to disk: failed to pickle "
                            "output. In version 1.5 this will raise an "
                            f"exception. Exception: {e}.",
                            FutureWarning
                        )

            self._concurrency_safe_write(item, filename, write_func)
        except Exception as e:  # noqa: E722
            warnings.warn(
                "Unable to cache to disk. Possibly a race condition in the "
                f"creation of the directory. Exception: {e}.",
                CacheWarning
            )


register_store_backend(FileSystemStoreBackendNoNumpy.NAME, FileSystemStoreBackendNoNumpy)


In [22]:
import time
from http.client import RemoteDisconnected

import requests
from joblib import Memory
from urllib3.exceptions import ProtocolError


SPARQL_API_URL = "http://127.0.0.1:7001"
CACHE_DIRECTORY = "wikidata/cache"

logger = logging.getLogger()
memory = Memory(CACHE_DIRECTORY, verbose=0, backend=FileSystemStoreBackendNoNumpy.NAME)


def execute_wiki_request_with_delays(api_url, params, headers):
    response = requests.get(
        api_url,
        params=params,
        headers=headers,
    )
    to_sleep = 0.2
    while response.status_code == 429:
        logger.warning(
            {
                "msg": f"Request to wikidata endpoint failed. Retry.",
                "params": params,
                "endpoint": api_url,
                "response": {
                    "status_code": response.status_code,
                    "headers": dict(response.headers),
                },
                "retry_after": to_sleep,
            }
        )
        if "retry-after" in response.headers:
            to_sleep += int(response.headers["retry-after"])
        to_sleep += 0.5
        time.sleep(to_sleep)
        response = requests.get(
            api_url,
            params=params,
            headers=headers,
        )

    return response


@memory.cache(ignore=['api_url'])
def execute_sparql_request(request: str, api_url: str = SPARQL_API_URL):
    params = {"format": "json", "query": request}
    headers = {
        "Accept": "application/sparql-results+json",
        "User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_11_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/50.0.2661.102 Safari/537.36",
    }
    logger.info(
        {
            "msg": "Send request to Wikidata",
            "params": params,
            "endpoint": api_url,
            "request": request
        }
    )
    try:
        response = execute_wiki_request_with_delays(api_url, params, headers)
    except (ProtocolError, RemoteDisconnected, requests.exceptions.ConnectionError) as e:
        logger.error(
            {
                "msg": str(e),
                "request": request,
                "endpoint": api_url,
            }
        )
        return None

    try:
        response = response.json()["results"]["bindings"]
        logger.debug(
            {
                "msg": "Received response from Wikidata",
                "params": params,
                "endpoint": api_url,
                "request": request,
                "response": response
            }
        )
        return response
    except Exception as e:
        logger.error(
            {
                "msg": str(e),
                "params": params,
                "endpoint": api_url,
                "response": {
                    "status_code": response.status_code,
                    "headers": dict(response.headers),
                },
            }
        )
        raise e

def get_label(entity_id):
    query = """
    PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
    PREFIX wd: <http://www.wikidata.org/entity/> 
    SELECT DISTINCT ?label
    WHERE {
        wd:<ENTITY> rdfs:label ?label
    } 
    """.replace(
        "<ENTITY>", entity_id
    )
    
    for lbl_obj in execute_sparql_request(query):
        if lbl_obj['label']['xml:lang'] == 'en':
            return lbl_obj['label']['value']

In [25]:
dataset = dataset.map(
    lambda record: {'object_label': get_label(record['object'])}
)

Map:   0%|          | 0/19481 [00:00<?, ? examples/s]

Map: 100%|██████████| 5622/5622 [00:15<00:00, 352.59 examples/s]


In [35]:
dataset.push_to_hub('s-nlp/sqwd', 'answerable', set_default=True)

Uploading the dataset shards: 100%|██████████| 1/1 [00:01<00:00,  1.73s/it]


CommitInfo(commit_url='https://huggingface.co/datasets/s-nlp/sqwd/commit/680b8199969fc0389fc96feb4f3b8be15b2674d0', commit_message='Upload dataset', commit_description='', oid='680b8199969fc0389fc96feb4f3b8be15b2674d0', pr_url=None, pr_revision=None, pr_num=None)